# Milestone 3: City Data ETL -- Trees

In [ ]:
# Read in datasets
import pandas as pd
df_historical_311 = pd.read_csv('311_OPCD_Calls__2012-Present__20241022 (1).csv')
df_francine_311 = pd.read_csv('311_OPCD_Francine_Calls_20241029.csv')
df_trees = pd.read_csv('Tree_Locations.csv')

In [ ]:
# Combine 311 datasets into one, dropping the duplicates
df_311 = pd.concat([df_historical_311, df_francine_311], ignore_index=True)
df_311 = df_311.drop_duplicates(subset='Service Request #', keep='first')

In [ ]:
# Filter the 311 dataset to only include the reason types relating to trees
df_311 = df_311[df_311['Request Reason'].isin(['Request Tree Service (Right of Way/Public Property)',
       'Tree Stump (removal, grind)',
       'Hurricane Francine Tree-Related Issues or Emergencies',
       'Trucks hitting overhead oak tree limbs',
       'Sidewalk repair after tree removal',
       'Oak tree blocking water line',
       'Tree roots'])]

#The "Status" column gives us a more detailed status of the tree,
# whereas "Request Status" tells us whether the request is active or not (Pending vs Closed).
df_311_closed = df_311[df_311['Request Status'] == 'Closed']
df_311_open = df_311[df_311["Request Status"] == 'Pending']

df_311_open

print(f"Number of open tickets: {len(df_311_open)}, about {((len(df_311_open)/len(df_311))*100):.2f}% of all 311 tree-related reports since 2012.")
print(f"Number of closed tickets: {len(df_311_closed)}")


Number of open tickets: 6169, about 23.01% of all 311 tree-related reports since 2012.
Number of closed tickets: 20639


In [ ]:
# Possible (detailed): statuses for open tickets
df_311_open["Status"].unique()

array(['Inspected', 'Pending', nan, 'Stump', 'Assigned to Contractor',
       'Wrong Agency'], dtype=object)

In [ ]:
df_311_open.head()

/usr/local/lib/python3.10/dist-packages/google/colab/_dataframe_summarizer.py:88: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  cast_date_col = pd.to_datetime(column, errors="coerce")


Service Request #      Request Type  \
0       2021-843811  Parks & Parkways   
1       2021-843700  Parks & Parkways   
2       2021-842098  Parks & Parkways   
4       2022-858762  Parks & Parkways   
7       2022-857748  Parks & Parkways   

                                      Request Reason            Date Created  \
0  Request Tree Service (Right of Way/Public Prop...  11/23/2021 09:20:55 AM   
1  Request Tree Service (Right of Way/Public Prop...  11/22/2021 02:01:39 PM   
2  Request Tree Service (Right of Way/Public Prop...  11/15/2021 09:01:27 AM   
4  Request Tree Service (Right of Way/Public Prop...  02/04/2022 12:07:07 AM   
7  Request Tree Service (Right of Way/Public Prop...  01/31/2022 10:51:55 AM   

            Date Modified Date Closed Request Status  \
0  12/10/2021 02:14:16 PM         NaN        Pending   
1  12/10/2021 01:39:00 PM         NaN        Pending   
2  12/10/2021 11:05:30 AM         NaN        Pending   
4  02/04/2022 12:11:06 AM         NaN        Pending   
7  03/15/2022 12:01:09 PM         NaN        Pending   

              Responsible Agency                      Address  \
0  Department of Parks & Parkway             4045 Iroquois St   
1  Department of Parks & Parkway             6131 Coliseum St   
2  Department of Parks & Parkway              1140 Seventh St   
4  Department of Parks & Parkway  FAIRFAX PL & WESTCHESTER ST   
7  Department of Parks & Parkway         6478 General Diaz St   

  Council District     Status Contractor Contractor Action   RowID  \
0                D  Inspected        NaN               NaN  843811   
1                A  Inspected        NaN               NaN  843700   
2                B  Inspected        NaN               NaN  842098   
4                C    Pending        NaN               NaN  858762   
7                A  Inspected        NaN               NaN  857748   

              X              Y  Longitude   Latitude  \
0  3.689163e+06  548192.398994 -90.043281  30.001104   
1  3.664278e+06  520525.948408 -90.122819  29.925777   
2  3.676162e+06  520609.486648 -90.085301  29.925656   
4  3.705978e+06  517436.780000 -89.991300  29.916006   
7  3.669721e+06  550565.669716 -90.104620  30.008217   

                                   Location  
0  (30.001103978875168, -90.04328085495841)  
1  (29.925777224098525, -90.12281884827456)  
2  (29.925656352017338, -90.08530058909707)  
4   (29.916005894169643, -89.9913000343529)  
7   (30.00821718816477, -90.10461997207399)

In [ ]:
df_trees.head()

OBJECTID   TREE_ID                            COMMON  \
0         1   122-174                      Bald Cypress   
1         2   122-379  Crape Myrtle (including hybrids)   
2         3   122-380  Crape Myrtle (including hybrids)   
3         4   122-528  Crape Myrtle (including hybrids)   
4         5  122-1195               Oriental Arborvitae   

                            BOTANICAL  \
0                  Taxodium distichum   
1  Lagerstroemia indica (and hybrids)   
2  Lagerstroemia indica (and hybrids)   
3  Lagerstroemia indica (and hybrids)   
4              Platycladus orientalis   

                                      Shape  
0   (29.99581246500003, -90.06134918699996)  
1  (30.004995531000077, -90.06117877099996)  
2  (30.005057347000047, -90.06111208799996)  
3  (30.001924020000047, -90.06142478499999)  
4  (29.988632602000052, -90.06226613899997)

#Preliminary Mapping of Trees & Open 311 Tickets on a Map

In [ ]:
import plotly.express as px
import pandas as pd
import plotly.graph_objects as go


new_orleans_center = {"lon": -90.07, "lat": 29.95}


df_trees[['Latitude', 'Longitude']] = df_trees['Shape'].str.extract(r'\(([^,]+), ([^)]+)\)').astype(float)

fig = go.Figure()

fig.add_trace(
    go.Scattermapbox(
        lat=df_trees['Latitude'],
        lon=df_trees['Longitude'],
        mode='markers',
        marker=dict(size=3, color='green'),
        name='Tree Locations'
    )
)

fig.add_trace(
    go.Scattermapbox(
        lat=df_311_open.Latitude,
        lon=df_311_open.Longitude,
        text=df_311_open.Address,
        mode='markers',
        marker=dict(size=3, color='red'),
        name='Open Tree-Related 311 Reports'
  )
)

fig.update_layout(
    mapbox=dict(center=new_orleans_center, zoom=11, style="open-street-map")
)

fig.show()